In [1]:
import numpy as np
import pandas as pd
from sklearn.linear_model import LinearRegression
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
import optuna
from optuna.samplers import TPESampler
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_error

from plotly.io import show

# ARIM-Academy：　機器データ利活用ユースケース
### 機器：誘導結合プラズマ発光分光分析法（ICP-OES）
### 分析：次元削減、クラスタ分析


## データセット

    
本編で扱う 『茶の元素分析データセット』（data.xlsx）、は、ブラックセイロン(BC)、ブラックトルコ(BT)、グリーンセイロン(GC)、グリーントルコ(GT)の4種類の茶葉について、3つの濃度（1%、2%、3%）で抽出したサンプルの誘導結合プラズマ発光分光分析法（ICP-OES）の元素分析データです。[1]

この研究では、機械学習（回帰分析としてMLR, ANN、および主成分分析、ISOMAP、階層クラスタ分析など）の手法を使い、茶の品種、濃度、浸出時間によるミネラル組成の変化を調査し、特定のミネラルレベルを調整する条件を見つける検討が行われています。

[1] Durmus, Y., Atasoy, A.D. & Atasoy, A.F. Mathematical optimization of multilinear and artificial neural network regressions for mineral composition of different tea types infusions. Sci Rep 14, 18285 (2024). https://doi.org/10.1038/s41598-024-69149-1

---
<br>  
<img src="./img/main_image.jpg" width="50%">
<br> 

---

**Chemical composition** 
* 9種類の元素分析値（Al, Ca, Cu, Fe,K,Mg,Mn,Na,Zn） 

**Experimental parameters**  
* Concentration：　お茶の濃度
* time:　抽出時間

**Label**
* grouped:　品種・色・濃度・抽出時間を識別できる一種の飼料名（MLは使用せず） 
* teaConc:　濃度ラベル（MLは使用せず）
* tea_org:　色ラベル（MLは使用せず）
* tea_var:　品種ラベル（MLは使用せず）
* tea：　　 色と品種ラベル（MLで使用）

### 教材への接続
google colabにおけるオンラインの場合にこのラインを実行します。（<font color="red">Google colabに接続しない場合には不要</font>）

In [ ]:
!git clone https://github.com/ARIM-Usecase/Example_2.git
%cd Example_2

### ライブラリのインポート
コード実行で必要なpythonのライブラリをimport文でロードします。

## 1.データセットの読み込みと前処理


### サンプルファイルの読み込み
pandasライブラリのread_excel()関数は、Excelファイルを読み込んでpandasのDataFrame形式に変換する関数です。ここでは[data]フォルダーにあるdata.xlsxファイルをDataFrameとして読み込み、その結果をdfという変数に格納します。168のサンプルに対して16の特徴量からなるデータ行列となっています。

In [4]:
# データの読み込み
data = pd.read_excel('./data/data.xlsx', header = 1)

# 特徴量とターゲットの分離
X = data[['Concentration', 'time']]
y_Fe = data['Fe']
y_Al = data['Al']
y_Mn = data['Mn']

### Optuna目的関数の定義

In [5]:
# 目的関数の定義 (MLR 用)
def objective_mlr(trial):
    # MLR モデルの定義
    model = LinearRegression()

    # 試行による最適化パラメータ
    X_train = pd.DataFrame({
        'Concentration': [trial.suggest_float('Concentration', 1.0, 3.0)],
        'time': [trial.suggest_float('time', 2.0, 60.0)]
    })
    
    # モデルのトレーニング
    model.fit(X, y_Fe)

    # 予測
    y_pred_Fe = model.predict(X_train)
    y_pred_Al = model.predict(X_train)
    y_pred_Mn = model.predict(X_train)

    # 目的関数の計算（Fe の最大化、Al の最小化、Mn の安定化）
    return -((y_pred_Fe[0] - y_pred_Al[0]) - abs(y_pred_Mn[0] - 5.3))

### Optuna最適化実行

In [6]:
# Optunaによる最適化 (MLR)
study_mlr = optuna.create_study(direction='minimize', sampler=TPESampler())
study_mlr.optimize(objective_mlr, n_trials=500)

# 最適解の表示
print(f"MLR 最適解: {study_mlr.best_params}")

[I 2024-09-15 16:03:23,255] A new study created in memory with name: no-name-33183972-8498-466b-acdd-1c7ed9c88244
[I 2024-09-15 16:03:23,262] Trial 0 finished with value: 5.17341304723947 and parameters: {'Concentration': 2.434739895036183, 'time': 5.386972100499893}. Best is trial 0 with value: 5.17341304723947.
[I 2024-09-15 16:03:23,272] Trial 1 finished with value: 5.179519952563267 and parameters: {'Concentration': 1.9484790501141662, 'time': 12.836202767293535}. Best is trial 0 with value: 5.17341304723947.
[I 2024-09-15 16:03:23,276] Trial 2 finished with value: 5.1726735048615335 and parameters: {'Concentration': 1.3864352862489435, 'time': 30.565729164336236}. Best is trial 2 with value: 5.1726735048615335.
[I 2024-09-15 16:03:23,282] Trial 3 finished with value: 5.179289612551003 and parameters: {'Concentration': 1.6934854658965661, 'time': 18.993866107129563}. Best is trial 2 with value: 5.1726735048615335.
[I 2024-09-15 16:03:23,291] Trial 4 finished with value: 5.203674356

MLR 最適解: {'Concentration': 2.999924639857367, 'time': 59.99966823307885}


### 可視化プロット

In [7]:
# 結果のプロット (オプション)
fig = optuna.visualization.plot_optimization_history(study_mlr)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)

In [8]:
# 結果のプロット (オプション)
fig = optuna.visualization.plot_contour(study_mlr)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)


In [9]:
import numpy as np
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Input

# 目的関数の定義 (ANN 用)
def objective_ann(trial):
    # ANN モデルの定義
    model = Sequential()
    model.add(Input(shape=(2,)))  # input_dim の代わりに Input レイヤーを使用
    model.add(Dense(16, activation='relu'))
    model.add(Dense(16, activation='relu'))
    model.add(Dense(1, activation='linear'))

    # 最適化アルゴリズムと損失関数
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])

    # 試行による最適化パラメータ
    X_train = np.array([[trial.suggest_float('Concentration', 1.0, 3.0),
                         trial.suggest_float('time', 2.0, 60.0)]])
    
    # モデルのトレーニング
    model.fit(X, y_Fe, epochs=10, verbose=0)

    # 予測
    y_pred_Fe = model.predict(X_train)
    y_pred_Al = model.predict(X_train)
    y_pred_Mn = model.predict(X_train)

    # 目的関数の計算（Fe の最大化、Al の最小化、Mn の安定化）
    return -((y_pred_Fe[0][0] - y_pred_Al[0][0]) - abs(y_pred_Mn[0][0] - 5.3))


In [10]:
# Optunaによる最適化 (ANN)
study_ann = optuna.create_study(direction='minimize', sampler=TPESampler())
study_ann.optimize(objective_ann, n_trials=100)

[I 2024-09-15 16:04:02,586] A new study created in memory with name: no-name-96d330ca-5919-4706-8ce4-8ac78a4e735c


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step


[I 2024-09-15 16:04:04,208] Trial 0 finished with value: 5.896977710723877 and parameters: {'Concentration': 2.201681403195753, 'time': 23.795032080831053}. Best is trial 0 with value: 5.896977710723877.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step


[I 2024-09-15 16:04:05,718] Trial 1 finished with value: 4.947086083889007 and parameters: {'Concentration': 2.792931901719983, 'time': 34.479986089433666}. Best is trial 1 with value: 4.947086083889007.


...

[I 2024-09-15 16:07:34,627] Trial 97 finished with value: 5.558636772632599 and parameters: {'Concentration': 1.7432940135421737, 'time': 56.545649778709546}. Best is trial 66 with value: 0.9272673606872557.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step


[I 2024-09-15 16:07:35,799] Trial 98 finished with value: 4.95654918551445 and parameters: {'Concentration': 1.799828817683587, 'time': 43.41018956593092}. Best is trial 66 with value: 0.9272673606872557.


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 77ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step


[I 2024-09-15 16:07:37,053] Trial 99 finished with value: 5.058821830153465 and parameters: {'Concentration': 2.083725126427441, 'time': 51.796339058644}. Best is trial 66 with value: 0.9272673606872557.


In [10]:
print(f"ANN 最適解: {study_ann.best_params}")

ANN 最適解: {'Concentration': 2.3076776679604682, 'time': 22.587271456539913}


In [12]:

# 結果のプロット (オプション)
fig = optuna.visualization.plot_optimization_history(study_ann)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)


In [14]:


# 結果のプロット (オプション)
fig = optuna.visualization.plot_contour(study_ann)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)


In [11]:
fig = optuna.visualization.plot_slice(study_ann)
fig.update_layout(width=800, height=600, showlegend=False)  # 凡例を非表示に設定
show(fig)
